# Daten Extraktion aus dem Bundesanzeiger

## Vorbereitung

In [64]:
import pandas as pd

from aki_prj23_transparenzregister.utils.data_extraction.bundesanzeiger import (
    Bundesanzeiger,
)

ba_wrapper = Bundesanzeiger()
# df_reports = ba_wrapper.get_information("Törmer Energy Solar 1 GmbH & Co. KG", "")
df_reports = ba_wrapper.get_information("Atos IT-Dienstleistung und Beratung GmbH", "")
df_reports.head()

date                                   company  \
0 2023-07-07  Atos IT-Dienstleistung und Beratung GmbH   
2 2023-05-10  Atos IT-Dienstleistung und Beratung GmbH   
4 2022-03-25  Atos IT-Dienstleistung und Beratung GmbH   
5 2021-03-11  Atos IT-Dienstleistung und Beratung GmbH   
6 2020-03-24  Atos IT-Dienstleistung und Beratung GmbH   

                                          raw_report  jahr  \
0  <div class="publication_container">\n <div cla...  2021   
2  <div class="publication_container">\n <div cla...  2021   
4  <div class="publication_container">\n <div cla...  2020   
5  <div class="publication_container">\n <div cla...  2019   
6  <div class="publication_container">\n <div cla...  2018   

                                            auditors  \
0                                                 []   
2  [Auditor(name='Eckhard Lewe', company='Grant T...   
4  [Auditor(name='Eckhard Lewe', company='Warth &...   
5  [Auditor(name='Eckhard Lewe', company='Warth &...   
6  [Auditor(name='Ulrich Diersch', company='Warth...   

                                   financial_results  
0                                                 {}  
2    {'equity': 23295.0, 'current_assets': 111516.0}  
4     {'equity': 23296.0, 'current_assets': 93901.0}  
5  {'net_income': 0.0, 'equity': 23296.0, 'curren...  
6  {'net_income': 0.0, 'equity': 23296.0, 'curren...

## Daten Extraktion

In [65]:
from bs4 import BeautifulSoup
from io import StringIO

In [68]:
sample_report = df_reports.iloc[1].raw_report

### Aufsichtsrat

**TODO**

### Bilanz bzw. GuV

In [163]:
def parse_tables(report: str) -> list:
    result = []
    soup = BeautifulSoup(report, features="html.parser")
    for table in soup.find_all("table", {"class": "std_table"}):
        df = pd.read_html(StringIO(str(table)), flavor="bs4")[0]
        print(df.columns)
        print(df.dtypes)
        result.append(df)
    return result


tables = parse_tables(sample_report)

Index([0, 1], dtype='int64')
0    object
1    object
dtype: object
Index(['Unnamed: 0', 'Anhang', '31.12.2021  TEUR', 'Vorjahr  TEUR'], dtype='object')
Unnamed: 0          object
Anhang              object
31.12.2021  TEUR    object
Vorjahr  TEUR       object
dtype: object
Index(['Unnamed: 0', 'Anhang', '2021  TEUR', 'Vorjahr  TEUR'], dtype='object')
Unnamed: 0        object
Anhang            object
2021  TEUR       float64
Vorjahr  TEUR    float64
dtype: object
Index(['Aufgliederung nach Tätigkeitsbereichen', '2021  TEUR',
       'Vorjahr  TEUR'],
      dtype='object')
Aufgliederung nach Tätigkeitsbereichen     object
2021  TEUR                                float64
Vorjahr  TEUR                             float64
dtype: object
Index(['Aufgliederung nach Inland und Ausland', '2021  TEUR', 'Vorjahr  TEUR'], dtype='object')
Aufgliederung nach Inland und Ausland     object
2021  TEUR                               float64
Vorjahr  TEUR                            float64
dtype: object
In

In [164]:
current_table = tables[1]
current_table.head()

Unnamed: 0 Anhang 31.12.2021  TEUR Vorjahr  TEUR
0                     A. Anlagevermögen    NaN              NaN           NaN
1  I. Immaterielle Vermögensgegenstände    NaN              NaN           NaN
2        Entgeltlich erworbene Software    NaN                3             6
3                       II. Sachanlagen    NaN              NaN           NaN
4             1. Grundstücke und Bauten    NaN               75            89

In [165]:
import re


def cleanse_string(value: str) -> str:
    print(value)
    if value is not None and isinstance(value, str):
        return re.sub(r"(.+\.).", "", value)
    return None

In [166]:
for index, row in current_table.iterrows():
    current_table.iloc[index][0] = cleanse_string(row[0])
current_table.head()

A. Anlagevermögen
I. Immaterielle Vermögensgegenstände
Entgeltlich erworbene Software
II. Sachanlagen
1. Grundstücke und Bauten
2. Technische Anlagen und Maschinen
3. Andere Anlagen, Betriebs- und Geschäftsausstattung
4. Geleistete Anzahlung und Anlagen im Bau
nan
III. Finanzanlagen
Sonstige Ausleihungen
nan
B. Umlaufvermögen
I. Vorräte
Waren
II. Forderungen und sonstige Vermögensgegenstände
1. Forderungen aus Lieferungen und Leistungen
2. Forderungen gegen verbundene Unternehmen
3. Sonstige Vermögensgegenstände
nan
nan
C. Rechnungsabgrenzungsposten
D. Aktiver Unterschiedsbetrag aus der Vermögensverrechnung
nan
Passiva
nan
A. Eigenkapital
I. Gezeichnetes Kapital
II. Kapitalrücklage
III. Gewinnrücklagen
Andere Gewinnrücklagen
IV. Gewinnvortrag
nan
B. Rückstellungen
1. Rückstellungen für Pensionen
2. Steuerrückstellungen
3. Sonstige Rückstellungen
nan
C. Verbindlichkeiten
1. Erhaltene Anzahlungen
2. Verbindlichkeiten aus Lieferungen und Leistungen
3. Verbindlichkeiten gegenüber verbunden

C:\Users\trist\AppData\Local\Temp\ipykernel_18940\152097142.py:2: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  current_table.iloc[index][0] = cleanse_string(row[0])
C:\Users\trist\AppData\Local\Temp\ipykernel_18940\152097142.py:2: FutureWarning: Series.__setitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To set a value by position, use `ser.iloc[pos] = value`
  current_table.iloc[index][0] = cleanse_string(row[0])


Unnamed: 0 Anhang 31.12.2021  TEUR Vorjahr  TEUR
0                     Anlagevermögen    NaN              NaN           NaN
1  Immaterielle Vermögensgegenstände    NaN              NaN           NaN
2     Entgeltlich erworbene Software    NaN                3             6
3                        Sachanlagen    NaN              NaN           NaN
4             Grundstücke und Bauten    NaN               75            89

In [167]:
def parse_string_to_float(value) -> float:
    try:
        if value is None:
            return None
        if isinstance(value, float):
            return value
        return float(value.replace(".", "").replace(",", "."))
    except Exception as e:
        return None


def apply_factor(value, factor: float):
    transformed_value = parse_string_to_float(value)
    if transformed_value is None or isinstance(transformed_value, str):
        return None
    result = transformed_value * factor
    # print(result)
    return result

In [168]:
converter = {"T€": 1 / 1000, "TEUR": 1000, "EUR": 1 / 1000, "€": 1}

for column in current_table.columns:
    if isinstance(column, tuple):
        for c in column:
            for x, factor in converter.items():
                if x in c:
                    current_table[column] = current_table[column].apply(
                        lambda x: apply_factor(x, factor)
                    )
                    next
    else:
        for x, factor in converter.items():
            parts = column.split(" ")
            for y in parts:
                if re.match(x, y):
                    current_table[column] = current_table[column].apply(
                        lambda x: apply_factor(x, factor)
                    )
                    current_table.rename({column: parts[0]}, inplace=True, axis=1)
                    next
                # print(current_table[column])
current_table.dropna(axis=0, how="all", inplace=True)
current_table.head()

Unnamed: 0 Anhang  31.12.2021  Vorjahr
0                     Anlagevermögen    NaN         NaN      NaN
1  Immaterielle Vermögensgegenstände    NaN         NaN      NaN
2     Entgeltlich erworbene Software    NaN      3000.0   6000.0
3                        Sachanlagen    NaN         NaN      NaN
4             Grundstücke und Bauten    NaN     75000.0  89000.0

In [169]:
import re


def get_bilanz(report: str) -> any:
    result = {}
    soup = BeautifulSoup(report, features="html.parser")
    for pos in ["Aktiva", "Passiva"]:
        tag = soup.find("b", string=re.compile(pos))
        if tag:
            pos_results = pd.read_html(
                StringIO(str(tag.findNext("table", {"class": "std_table"})))
            )[0]
            result[pos] = pos_results
        else:
            result[pos] = pd.DataFrame([])
    return result

In [170]:
bilanz = get_bilanz(sample_report)
bilanz["Passiva"].head()

Unnamed: 0 Anhang  2021  TEUR  \
0                                    1. Umsatzerlöse    (1)      66.767   
1  2. Veränderung des Bestandes an unfertigen Lei...    NaN       0.000   
2                   3. Sonstige betriebliche Erträge    (2)     621.000   
3                                 4. Materialaufwand    NaN         NaN   
4                 a) Aufwendungen für bezogene Waren    NaN    -475.000   

   Vorjahr  TEUR  
0         69.819  
1        -41.000  
2        489.000  
3            NaN  
4         -1.220

In [171]:
bilanz["Aktiva"].head()

Unnamed: 0 Anhang 31.12.2021  TEUR Vorjahr  TEUR
0                     A. Anlagevermögen    NaN              NaN           NaN
1  I. Immaterielle Vermögensgegenstände    NaN              NaN           NaN
2        Entgeltlich erworbene Software    NaN                3             6
3                       II. Sachanlagen    NaN              NaN           NaN
4             1. Grundstücke und Bauten    NaN               75            89

In [172]:
from IPython.display import display, HTML

# Assuming that dataframes df1 and df2 are already defined:
display(HTML(bilanz["Passiva"].to_html()))

In [173]:
def get_tables(raw_report: str) -> list:
    soup = BeautifulSoup(raw_report, features="html.parser")
    tables = soup.find_all("table", {"class": "std_table"})
    dfs = []
    for table in tables:
        for df in pd.read_html(StringIO(str(table))):
            dfs.append(df)
    return dfs


for df in get_tables(sample_report):
    print(df.columns)

tables = get_tables(sample_report)

Index([0, 1], dtype='int64')
Index(['Unnamed: 0', 'Anhang', '31.12.2021  TEUR', 'Vorjahr  TEUR'], dtype='object')
Index(['Unnamed: 0', 'Anhang', '2021  TEUR', 'Vorjahr  TEUR'], dtype='object')
Index(['Aufgliederung nach Tätigkeitsbereichen', '2021  TEUR',
       'Vorjahr  TEUR'],
      dtype='object')
Index(['Aufgliederung nach Inland und Ausland', '2021  TEUR', 'Vorjahr  TEUR'], dtype='object')
Index(['Unnamed: 0', '31.12.2021  TEUR', 'Vorjahr  TEUR'], dtype='object')
Index(['Unnamed: 0', '31.12.2021  TEUR', 'Vorjahr  TEUR'], dtype='object')
Index(['Unnamed: 0', '31.12.2021'], dtype='object')
Index(['Unnamed: 0', 'TEUR'], dtype='object')
Index(['Unnamed: 0', 'TEUR'], dtype='object')
Index(['Unnamed: 0', 'TEUR'], dtype='object')
Index([0, 1, 2], dtype='int64')
Index(['Unnamed: 0', 'TEUR'], dtype='object')
Index(['Unnamed: 0', '31.12.2021  TEUR', 'Vorjahr  TEUR'], dtype='object')
Index(['Unnamed: 0', '2021 Anzahl MA', 'Vorjahr Anzahl MA'], dtype='object')
MultiIndex([('Art des Geschäfts